In [ ]:
# Import the torch module for tensor computation and deep learning
import torch

# Import the matplotlib.pyplot module for creating static, animated, and interactive visualizations in Python
import matplotlib.pyplot as plt

# Import the numpy module for numerical operations in Python
import numpy as np

# Import the nn module from torch for building neural networks
import torch.nn as nn

# Import the transformers, datasets, evaluate, datasets, huggingface_hub modules for working with transformer models, datasets, evaluation metrics, and Hugging Face's hub
import transformers
import datasets
import evaluate
import datasets
import huggingface_hub

# Import the ColorJitter class from torchvision.transforms for randomly changing the brightness, contrast, and saturation of an image
from torchvision.transforms import ColorJitter

# Import the load_dataset function from the datasets module for loading datasets
from datasets import load_dataset

# Import the TrainingArguments and Trainer classes from the transformers module for setting training arguments and training transformer models
from transformers import TrainingArguments, Trainer

# Import the notebook_login function from the huggingface_hub module for logging in to Hugging Face's hub
from huggingface_hub import notebook_login

# Import the accelerate module for accelerating PyTorch code with mixed precision and distributed training
import accelerate

# Import the Accelerator class from the accelerate module for accelerating PyTorch code
from accelerate import Accelerator

# Import the pipeline function from the transformers module for creating a pipeline that processes and returns the model's output
from transformers import pipeline

# Import the Image class from the PIL module for opening, manipulating, and saving many different image file formats
from PIL import Image

# Import the glob function from the glob module for finding all the pathnames matching a specified pattern
from glob import glob

# Import the SegformerImageProcessor, SegformerModel, SegformerConfig, AutoImageProcessor, SegformerForSemanticSegmentation classes from the transformers module for working with Segformer models
from transformers import SegformerImageProcessor, SegformerModel, SegformerConfig, AutoImageProcessor, SegformerForSemanticSegmentation

# Set the allow_tf32 attribute of torch.backends.cuda.matmul to True to allow TensorFloat-32 (TF32) on Ampere devices
torch.backends.cuda.matmul.allow_tf32 = True

# Call the notebook_login function to log in to Hugging Face's hub
notebook_login()

# This code imports necessary modules and functions for a machine learning task. It sets up for tensor computations, deep learning, data visualization, working with transformer models, datasets, image manipulations, and more. It also logs into Hugging Face's hub.


In [ ]:
# Load a dataset from Hugging Face's hub using the specified repository name
ds = load_dataset("aashraychegu/glacier_scopes")

# Split the "train" subset of the dataset into a training set and a test set, with 5% of the data going to the test set
ds = ds["train"].train_test_split(.05)

# Assign the "train" subset of the split dataset to the variable train_ds
train_ds = ds["train"]

# Assign the "test" subset of the split dataset to the variable test_ds
test_ds = ds["test"]

# Define a dictionary mapping label IDs to their corresponding names
id2label = {
    "0": "sky",
    "1": "surface-to-bed",
    "2": "bed-to-bottom",
}

# Convert the keys of the id2label dictionary from strings to integers
id2label = {int(k): v for k, v in id2label.items()}

# Create a reverse mapping from label names to their corresponding IDs
label2id = {v: k for k, v in id2label.items()}

# Get the number of unique labels in the dataset
num_labels = len(id2label)

len(train_ds), len(test_ds)


In [ ]:
# Define the checkpoint from which to load the pre-trained model
checkpoint = "nvidia/MiT-b0"

# Load the image processor from the pre-trained checkpoint
image_processor = SegformerImageProcessor.from_pretrained(checkpoint)

# Load the Segformer model for semantic segmentation from the pre-trained checkpoint and move it to the GPU
model = SegformerForSemanticSegmentation.from_pretrained(
    checkpoint).to("cuda:0")

# Define the configuration for the test model, specifying the number of channels, labels, label-to-ID mapping, ID-to-label mapping, depths, hidden sizes, and decoder hidden size
test_config = SegformerConfig(num_channels=3, num_labels=num_labels, label2id=label2id,
                              id2label=id2label, depths=[2, 3, 4, 3], hidden_sizes=[64, 128, 320, 512], decoder_hidden_size=256*3)

# Load the image processor for the test model from the pre-trained checkpoint
test_image_processor = SegformerImageProcessor.from_pretrained(checkpoint)

# Create a Segformer model for semantic segmentation using the test configuration and move it to the GPU
test_model = SegformerForSemanticSegmentation(test_config).to("cuda:0")

# This code loads a pre-trained Segformer model and its image processor for semantic segmentation. It also sets up a test model with a specific configuration.


In [ ]:
# Set the device to be used for tensor computations to the first CUDA device
device = "cuda:0"


In [ ]:
# Define a ColorJitter object to randomly change the brightness, contrast, saturation, and hue of an image
jitter = ColorJitter(brightness=0.1, contrast=0.1, saturation=0.1, hue=0.1)

# Define a function to apply transformations to a batch of training examples


def train_transforms(example_batch):
    # Apply the jitter to each image in the batch and convert them to RGB
    images = [jitter(x.convert("RGB")) for x in example_batch["image"]]
    # Extract the labels from the batch
    labels = [x for x in example_batch["label"]]
    # Process the images and labels using the test image processor
    inputs = test_image_processor(images, labels)
    # Return the processed inputs
    return inputs

# Define a function to apply transformations to a batch of validation examples


def val_transforms(example_batch):
    # Convert each image in the batch to RGB
    images = [x.convert("RGB") for x in example_batch["image"]]
    # Extract the labels from the batch
    labels = [x for x in example_batch["label"]]
    # Process the images and labels using the test image processor
    inputs = test_image_processor(images, labels)
    # Return the processed inputs
    return inputs


# Set the transform function for the training dataset to be the train_transforms function
train_ds.set_transform(train_transforms)

# Set the transform function for the test dataset to be the val_transforms function
test_ds.set_transform(val_transforms)


In [ ]:
# Load the "mean_iou" metric for evaluating semantic segmentation models
metric = evaluate.load("mean_iou")

# Define a function to compute metrics for evaluation predictions
def compute_metrics(eval_pred):
    # Ensure that gradient computation is turned off, as it is not needed for evaluation
    with torch.no_grad():
        # Extract the logits and labels from the evaluation predictions
        logits, labels = eval_pred
        # Convert the logits to a PyTorch tensor
        logits_tensor = torch.from_numpy(logits)
        # Resize the logits tensor to match the size of the labels
        logits_tensor = nn.functional.interpolate(
            logits_tensor,
            size=labels.shape[-2:],
            mode="bilinear",
            align_corners=False,
        )
        # Take the argmax of the logits tensor along dimension 1 to get the predicted labels
        logits_tensor = logits_tensor.argmax(dim=1)
        # Detach the predicted labels from the computation graph and move them to the CPU
        pred_labels = logits_tensor.detach().cpu().numpy()
        # Compute the "mean_iou" metric for the predicted labels and the true labels
        metrics = metric.compute(
            predictions=pred_labels,
            references=labels,
            num_labels=num_labels,
            reduce_labels=False,
            ignore_index = 255
        )
        # Convert any numpy arrays in the metrics to lists
        for key, value in metrics.items():
            if type(value) is np.ndarray:
                metrics[key] = value.tolist()
        # Return the computed metrics
        return metrics

In [ ]:
# Define the training arguments
training_args = TrainingArguments(
    output_dir="glacformer",  # The output directory for the model predictions and checkpoints
    learning_rate=6e-5,  # The initial learning rate for Adam
    num_train_epochs=1,  # Total number of training epochs to perform
    auto_find_batch_size=True,  # Whether to automatically find an appropriate batch size
    save_total_limit=3,  # Limit the total amount of checkpoints and delete the older checkpoints
    eval_accumulation_steps=0,  # Number of steps to accumulate gradients before performing a backward/update pass
    evaluation_strategy="epoch",  # The evaluation strategy to adopt during training
    save_strategy="epoch",  # The checkpoint save strategy to adopt during training
    save_steps=1,  # Number of updates steps before two checkpoint saves
    eval_steps=1,  # Number of update steps before two evaluations
    logging_steps=30,  # Number of update steps before logging learning rate and other metrics
    remove_unused_columns=False,  # Whether to remove columns not used by the model when using a dataset
    fp16=True,  # Whether to use 16-bit float precision instead of 32-bit
    tf32=True,  # Whether to use tf32 precision instead of 32-bit
    gradient_accumulation_steps=4,  # Number of updates steps to accumulate before performing a backward/update pass
    hub_model_id = "aashraychegu/glacformer"  # The model ID on the Hugging Face model hub
)

# Define the trainer
trainer = Trainer(
    model=test_model,  # The model to train
    args=training_args,  # Training arguments
    train_dataset=train_ds,  # The training dataset
    eval_dataset=test_ds,  # The evaluation dataset
    compute_metrics=compute_metrics,  # The function that computes metrics
)

In [ ]:
# Start the training process
trainer.train()

In [ ]:
# Save the trained model to the specified directory
trainer.model.save_pretrained("glacformer")

# Create a repository object for the specified repository on Hugging Face's hub, cloning from the specified source
repo = huggingface_hub.Repository("glacformer", clone_from="aashraychegu/glacformer")

# Pull the latest changes from the remote repository
repo.git_pull()

# Push the local changes to the remote repository
repo.push_to_hub()

In [ ]:
# Define a function to combine images
def combine_images(images):
    # Convert images to HSV mode
    hsvimages = [img.convert('HSV') for img in images]

    # Define the hues for each image
    hues = [120, 200, 360]

    # Colorize each image with the corresponding hue
    for i, (img,limg) in enumerate(zip(hsvimages,images)):
        h, s, v = img.convert("HSV").split()
        h = h.point(lambda _: hues[i])
        s = s.point(lambda _: 255)
        img = Image.merge('HSV', (h, s, v)).convert('RGBA')
        img.putalpha(limg)
        images[i] = img

    # Combine the images
    combined_image = Image.alpha_composite(images[0], images[1])
    combined_image = Image.alpha_composite(combined_image, images[2])

    return combined_image

# Define a class for the model
class glacformer():
    def __init__(self, pipeline=pipeline("image-segmentation",
                                         model="aashraychegu/glacformer", image_processor="nvidia/MiT-b0"), image_list = glob("secondleg/*/cropped_images/*.png")) -> None:
        self.pipeline = pipeline
        self.image_list = image_list
    def __getitem__(self, index, alpha = 100):
        originals = [i["mask"] for i in self.pipeline(self.image_list[index])]
        segmap = combine_images(originals)
        segmap.putalpha(100)
        rgbaorig = Image.open(self.image_list[index]).convert("RGBA")
        rgbaorig.putalpha(255-alpha)
        return Image.alpha_composite(segmap,rgbaorig)
    def __len__(self):
        return len(self.image_list)
    def __iter__(self):
        for i in range(len(self)):
            yield self[i]
    def display(self, display):
        for i in evalmodel:
            display(i)
            if input("press enter to continue, anything else to stop") == "":
                continue
            else:
                break

# Create an instance of the model
evalmodel = glacformer()

# Import the display function from IPython
from IPython.display import display

# Display the model
glacformer.display(display)